In [1]:
import pandas as pd
import ast
from tqdm import tqdm
tqdm.pandas()

In [2]:
# Load Data
df_yake_claims = pd.read_json('/mnt/hdd01/patentsview/Patentsview - Cleantech Patents/Cleantech Concepts/Yake/g_patent_claims_cleantech_yake.json')

In [3]:
df_yake_claims.head()

patent_id                                     claim_fulltext  \
0   10000011   A method of reducing distortion in an additiv...   
1   10000017   A method for securing an attachment ( 3 , 33 ...   
2   10000021   A method for manufacturing a three-dimensiona...   
3   10000025   A method of laying up plies in an aircraft wi...   
4   10000033   A method of making a storage bag, comprising:...   

                                       keywords_yake  
0  [[shrinking supports, 0.0013617439], [part, 0....  
1  [[[adhesion surface, 0.0019894983000000002], [...  
2  [[[cavity metal mold, 0.0006303933], [predeter...  
3  [[[aircraft wing skin, 0.0008585078000000001],...  
4  [[[closure element, 0.002612919], [sidewall, 0...

In [4]:
# Iterate over rows in dataframe
for index, row in tqdm(df_yake_claims.iterrows()):
    # Cast row 'keywords_yake' column to string
    row['keywords_yake'] = str(row['keywords_yake']).lower()
    # Check if keywords_yake column starts with "[[[" and ends with "]]]""
    if row['keywords_yake'].startswith('[[[') and row['keywords_yake'].endswith(']]]'):
        # Remove first "[" and last "]" from keywords_yake column
        row['keywords_yake'] = row['keywords_yake'][1:-1]
    # Cast row 'keywords_yake' column to list
    row['keywords_yake'] = ast.literal_eval(row['keywords_yake'])
    # Assign modified 'keywords_yake' list to temporary variable
    keywords_yake_temp = row['keywords_yake']
    # Assign temporary variable to 'keywords_yake' column
    df_yake_claims.at[index, 'keywords_yake'] = keywords_yake_temp

515742it [01:10, 7302.58it/s]


In [5]:
df_yake_claims['keywords_yake_exploded'] = ''
# Iterate over rows in dataframe
for index,row in tqdm(df_yake_claims.iterrows()):
    # Check if 'keywords_yake' column is not a list
    if not isinstance(row['keywords_yake'], list):
        continue
    # Check if 'keywords_yake' column is an empty list or contains only empty lists
    if not any(keyword for keyword in row['keywords_yake']):
        continue
    # Iterate over keywords in 'keywords_yake' column and append to 'keywords_yake_exploded' column
    else:
        for keyword in row['keywords_yake']:
            df_yake_claims.at[index, 'keywords_yake_exploded'] += keyword[0] + ', '

515742it [02:04, 4143.47it/s]


In [6]:
keywords_list = []
min_yake_conf = 0.2

# Iterate over rows in dataframe
for index,row in tqdm(df_yake_claims.iterrows()):
    # Check if 'keywords_yake' column is not a list
    if not isinstance(row['keywords_yake'], list):
        continue
    # Check if 'keywords_yake' column is an empty list or contains only empty lists
    if not any(keyword for keyword in row['keywords_yake']):
        continue
    # Iterate over keywords in 'keywords_yake' column and append to 'keywords_yake_exploded' column
    else:
        for keyword in row['keywords_yake']:
            if keyword[1] <= min_yake_conf:
                keywords_list.append(keyword[0])

515742it [00:16, 31927.44it/s]


In [19]:
# Only consider alphanumeric characters in keywords
keywords_list = [
    keyword for keyword in keywords_list 
    if all(word.isalnum() for word in keyword.split())
]

In [6]:
# Cast 'keywords_yake_exploded' column to list
df_yake_claims['keywords_yake_exploded'] = df_yake_claims['keywords_yake_exploded'].str.split(', ')

In [10]:
# Delete last item in 'keywords_yake_exploded' cells
df_yake_claims['keywords_yake_exploded'] = df_yake_claims['keywords_yake_exploded'].apply(lambda x: x[:-1])

# Postprocessing

In [20]:
# Generate unique list of keywords
keywords_list_unique = list(set(keywords_list))
df_keywords_list_unique = pd.DataFrame(keywords_list_unique, columns=['keyword_yake'])

In [21]:
# Count absolute frequency of each keyword
from collections import Counter

# Step 1: Flatten the list of keywords into a single list
flattened_keywords = [keyword for keyword_list in tqdm(df_yake_claims['keywords_yake_exploded']) for keyword in keyword_list]

# Step 2: Use collections.Counter to count the occurrences of each keyword
keyword_counts = Counter(flattened_keywords)

# Step 3: Convert the keyword counts to a DataFrame
count_df = pd.DataFrame(keyword_counts.items(), columns=['keyword_yake', 'abs_frequency'])

# Step 4: Merge the count_df with df_keywords_list_unique on the 'keyword_yake' column
df_keywords_list_unique = df_keywords_list_unique.merge(count_df, on='keyword_yake', how='left')

100%|██████████| 515742/515742 [00:01<00:00, 440919.66it/s]


In [28]:
### MAYBE I NEED TO REDO THIS WITH FULL TEXT CLAIMS INSTEAD OF JUST THE YAKE KEYWORDS

# Calculate document frequency by dividing absolute frequency by len of df_yake_claims
df_keywords_list_unique['doc_frequency'] = df_keywords_list_unique['abs_frequency'] / len(df_yake_claims)

In [29]:
# Prune dataframe by document frequency and absolute frequency
min_abs_frequency = 5
max_abs_frequency = 1000
# max_doc_frequency = 0.3

df_keywords_list_unique_pruned = df_keywords_list_unique[(df_keywords_list_unique['abs_frequency'] >= min_abs_frequency) & (df_keywords_list_unique['abs_frequency'] <= max_abs_frequency)]

# Reset index
df_keywords_list_unique_pruned.reset_index(drop=True, inplace=True)

In [16]:
# Only consider n-grams with n >= 2
min_ngram_length = 2

# Generate copy of df_keywords_list_unique_pruned
df_keywords_list_unique_pruned = df_keywords_list_unique_pruned.copy()

def filter_keywords(keyword_string):
    # Split the keyword string into individual keywords
    keywords = keyword_string.split(', ')
    # Filter out keywords with fewer than 2 words
    filtered_keywords = [keyword for keyword in keywords if len(keyword.split()) >= min_ngram_length]
    # Join the filtered keywords back into a string
    return ', '.join(filtered_keywords)

# Create a copy of df_keywords_list_unique_pruned to avoid SettingWithCopyWarning
df_keywords_list_unique_pruned = df_keywords_list_unique_pruned.copy()

# Now use .loc to modify the 'keyword_yake' column
df_keywords_list_unique_pruned.loc[:, 'keyword_yake'] = df_keywords_list_unique_pruned['keyword_yake'].progress_apply(filter_keywords)

# Delete rows with empty 'keyword_yake' column
df_keywords_list_unique_pruned = df_keywords_list_unique_pruned[df_keywords_list_unique_pruned['keyword_yake'] != '']

# Reset index
df_keywords_list_unique_pruned.reset_index(drop=True, inplace=True)

100%|██████████| 31446/31446 [00:00<00:00, 1034341.71it/s]


In [33]:
import nltk
from nltk.corpus import stopwords

# Download stopwords
# nltk.download('stopwords')

# Generate copy of df_keywords_list_unique_pruned
df_keywords_list_unique_pruned = df_keywords_list_unique_pruned.copy()

# Delete all stopwords from 'keyword_yake' column
df_keywords_list_unique_pruned.loc[:, 'keyword_yake'] = df_keywords_list_unique_pruned['keyword_yake'].progress_apply(
    lambda x: ' '.join([word for word in x.split() if word not in (stopwords.words('english'))])
)

100%|██████████| 69623/69623 [00:07<00:00, 9157.19it/s]


In [34]:
### MAYBE I NEED TO REDO THIS PART WITH THE CLAIM TEXTS INSTEAD OF THE KEYWORDS

import spacy

# Download spacy model
nlp = spacy.load('en_core_web_sm')

# Ensure you're working on a new DataFrame, not a slice of an old one
df_keywords_list_unique_pruned_pos = df_keywords_list_unique_pruned.copy()

# Perform part-of-speech tagging on the 'keyword_yake' column 
# and save the POS tags in a new column 'keyword_yake_pos'
df_keywords_list_unique_pruned_pos['keyword_yake_pos'] = df_keywords_list_unique_pruned_pos['keyword_yake'].progress_apply(
    lambda x: [token.pos_ for token in nlp(x)]
)

/home/thiesen/Documents/Cleantech_Concepts/venv/lib64/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
100%|██████████| 69623/69623 [02:43<00:00, 425.47it/s]


In [35]:
# Filter out all keywords that do not contain NOUN, PRON or PROPN in their POS tags
df_keywords_list_unique_pruned_pos = df_keywords_list_unique_pruned_pos[df_keywords_list_unique_pruned_pos['keyword_yake_pos'].progress_apply(
    lambda x: any(pos in ['NOUN', 'PRON', 'PROPN'] for pos in x)
)]

# Reset index
df_keywords_list_unique_pruned_pos.reset_index(drop=True, inplace=True)

100%|██████████| 69623/69623 [00:00<00:00, 900848.74it/s]


In [36]:
import re

# Function to check if a word contains at least three consecutive capital letters (filter out all abbreviations)
def has_three_consecutive_caps(word):
    return re.search(r'[A-Z]{3,}', word) is not None

# Function to check if any word in an n-gram contains at least three consecutive capital letters
def check_ngram(ngram):
    return any(has_three_consecutive_caps(word) for word in ngram.split())

# Use the DataFrame `apply` method to filter rows
df_keywords_list_unique_pruned_pos_filtered = df_keywords_list_unique_pruned_pos[~df_keywords_list_unique_pruned_pos['keyword_yake'].progress_apply(check_ngram)]

100%|██████████| 62192/62192 [00:00<00:00, 506135.58it/s]


In [29]:
# # Test to filter out brown corpus words
# from nltk.corpus import brown
# # nltk.download('brown')

# # Step 1: Pre-calculate the set of Brown corpus words
# brown_words_set = set(brown.words())

# # Function to check if any word in a keyword phrase exists in the Brown corpus
# def check_brown_words(phrase):
#     return any(word in brown_words_set for word in phrase.split())

# # Step 2: Use progress_apply with the optimized function
# df_keywords_list_unique_pruned_pos_filtered_brown = df_keywords_list_unique_pruned_pos_filtered[
#     df_keywords_list_unique_pruned_pos_filtered['keyword_yake'].progress_apply(check_brown_words)
# ]

100%|██████████| 24303/24303 [00:00<00:00, 906299.02it/s]


# Keyword Embedding

In [37]:
from sentence_transformers import SentenceTransformer
import torch

In [38]:
model_climatebert = SentenceTransformer('climatebert/distilroberta-base-climate-f')
model_bertforpatents = SentenceTransformer('anferico/bert-for-patents')
model_patentsberta = SentenceTransformer('AI-Growth-Lab/PatentSBERTa')

No sentence-transformers model found with name /home/thiesen/.cache/torch/sentence_transformers/climatebert_distilroberta-base-climate-f. Creating a new one with MEAN pooling.
Some weights of RobertaModel were not initialized from the model checkpoint at /home/thiesen/.cache/torch/sentence_transformers/climatebert_distilroberta-base-climate-f and are newly initialized: ['roberta.pooler.dense.bias', 'roberta.pooler.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.
No sentence-transformers model found with name /home/thiesen/.cache/torch/sentence_transformers/anferico_bert-for-patents. Creating a new one with MEAN pooling.


In [39]:
# Check if GPU is available
if torch.cuda.is_available():
    device = torch.device("cuda")
    print("GPU available: {}".format(torch.cuda.get_device_name(0)))
else:
    device = torch.device("cpu")
    print("GPU not available, CPU used")

GPU available: NVIDIA RTX A4500


In [40]:
# Generate copy of df_keywords_list_unique_pruned_pos
df_keywords_list_unique_embeddings = df_keywords_list_unique_pruned_pos_filtered.copy()

# Perform sentence embedding on the 'keyword_yake' column
df_keywords_list_unique_embeddings['keyword_yake_patentsberta_embedding'] = df_keywords_list_unique_embeddings['keyword_yake'].progress_apply(
    lambda x: model_patentsberta.encode(x)
)

df_keywords_list_unique_embeddings['keyword_yake_climatebert_embedding'] = df_keywords_list_unique_embeddings['keyword_yake'].progress_apply(
    lambda x: model_climatebert.encode(x)
)

df_keywords_list_unique_embeddings['keyword_yake_bertforpatents_embedding'] = df_keywords_list_unique_embeddings['keyword_yake'].progress_apply(
    lambda x: model_bertforpatents.encode(x)
)

100%|██████████| 62192/62192 [26:12<00:00, 39.55it/s]


In [43]:
# Save dataframe to json
df_keywords_list_unique_embeddings.to_json('/mnt/hdd01/patentsview/Patentsview - Cleantech Patents/Cleantech Concepts/Yake/g_patent_claims_cleantech_yake_keywords_embeddings.json', orient='records')

# Match Keyword Dataframe and Patent Ids and CPC

In [7]:
df_cpc = pd.read_json('/mnt/hdd01/patentsview/Patentsview - Cleantech Patents/df_patentsview_patent_cpc_grouped_cleantech.json')

In [8]:
# Merge df_yake_claims with df_cpc only keep 'cpc' from df_cpc
df_yake_claims_cpc = df_yake_claims.merge(df_cpc[['patent_id', 'cpc']], on='patent_id', how='left')

In [11]:
rows_list = []

# Iterate over rows in dataframe
for index, row in tqdm(df_yake_claims_cpc.iterrows()):
    if row['keywords_yake_exploded'] == []:
        continue
    if not any(keyword for keyword in row['keywords_yake_exploded']):
        continue
    # Iterate over keywords in 'keywords_yake' column and append patent_id and cpc information
    else:
        for keyword in row['keywords_yake_exploded']:
            rows_list.append({'patent_id': row['patent_id'], 
                              'cpc': row['cpc'], 
                              'keyword_yake': keyword})

df_cpc_keywords = pd.DataFrame(rows_list)

515742it [00:39, 12940.41it/s]


In [13]:
# Extract 'cpc_subclass' into a new column
df_cpc_keywords['cpc_subclass'] = df_cpc_keywords['cpc'].progress_apply(
    lambda x: [entry['cpc_subclass'] for entry in x.values() if 'cpc_subclass' in entry]
)

# Extract 'cpc_group' into a new column
df_cpc_keywords['cpc_group'] = df_cpc_keywords['cpc'].progress_apply(
    lambda x: [entry['cpc_group'] for entry in x.values() if 'cpc_group' in entry]
)

100%|██████████| 5668637/5668637 [00:08<00:00, 691144.69it/s] 


In [14]:
# Aggregate df_cpc_keywords on 'keyword_yake' column
df_cpc_keywords_agg = df_cpc_keywords.groupby('keyword_yake').agg(
    patent_id_list = pd.NamedAgg(column='patent_id', aggfunc=list),
    cpc_subclass_list = pd.NamedAgg(column='cpc_subclass', aggfunc=list),
    cpc_group_list = pd.NamedAgg(column='cpc_group', aggfunc=list)
)

In [15]:
len(df_cpc_keywords_agg)

1321219

In [16]:
# Define a function to flatten nested lists
def flatten_nested_list(nested_list):
    return [item for sublist in nested_list for item in sublist]

# Convert nested lists in 'cpc_subclass_list' and 'cpc_group_list' columns to lists of strings
df_cpc_keywords_agg[['cpc_subclass_list', 'cpc_group_list']] = df_cpc_keywords_agg[['cpc_subclass_list', 'cpc_group_list']].applymap(flatten_nested_list)


/tmp/ipykernel_2391719/3934664484.py:6: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  df_cpc_keywords_agg[['cpc_subclass_list', 'cpc_group_list']] = df_cpc_keywords_agg[['cpc_subclass_list', 'cpc_group_list']].applymap(flatten_nested_list)


In [17]:
# Remove duplicates from 'cpc_subclass_list'
df_cpc_keywords_agg['cpc_subclass_list'] = df_cpc_keywords_agg['cpc_subclass_list'].progress_apply(lambda x: list(set(x)))

# Remove duplicates from 'cpc_group_list'
df_cpc_keywords_agg['cpc_group_list'] = df_cpc_keywords_agg['cpc_group_list'].progress_apply(lambda x: list(set(x)))

100%|██████████| 1321219/1321219 [00:01<00:00, 894601.12it/s]


In [18]:
df_keywords_list_unique_embeddings = pd.read_json('/mnt/hdd01/patentsview/Patentsview - Cleantech Patents/Cleantech Concepts/Yake/g_patent_claims_cleantech_yake_keywords_embeddings.json')

In [19]:
len(df_keywords_list_unique_embeddings)

62192

In [20]:
# Merge df_cpc_keywords_agg with df_keywords_list_unique_embeddings on 'keyword_yake' column and generate new dataframe
df_cpc_keywords_list_unique_embeddings = df_keywords_list_unique_embeddings.merge(df_cpc_keywords_agg, on='keyword_yake', how='left')

In [28]:
# # Remove rows with 'patent_id_list' = NaN
# df_cpc_keywords_list_unique_embeddings_filtered = df_cpc_keywords_list_unique_embeddings[~df_cpc_keywords_list_unique_embeddings['patent_id_list'].isna()]

In [23]:
df_cpc_keywords_list_unique_embeddings_filtered.to_json('/mnt/hdd01/patentsview/Patentsview - Cleantech Patents/Similarity Search - CPC Classification and Claims/df_keywords_y02_claims_embeddings_filtered.json')

# Dimensionality Reduction

In [4]:
# Load data if necessary
df_keywords_list_unique_pruned_embeddings = pd.read_json('/mnt/hdd01/patentsview/Patentsview - Cleantech Patents/Cleantech Concepts/Yake/g_patent_claims_cleantech_yake_keywords_embeddings.json')

## UMAP

In [2]:
import umap
import numpy as np
umap_dim = 2
reducer = umap.UMAP(random_state=42, n_components=umap_dim)

/home/thiesen/Documents/Cleantech_Concepts/venv/lib64/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [5]:
# Stack all the embeddings into a 2D array
embeddings_patentsberta = np.vstack(df_keywords_list_unique_embeddings['keyword_yake_patentsberta_embedding'].values)

# Perform UMAP dimensionality reduction
umap_embeddings_patentsberta = reducer.fit_transform(embeddings_patentsberta)

# Assign the reduced dimension embeddings back to new DataFrame columns
df_keywords_list_unique_embeddings_umap['keyword_yake_patentsberta_embedding_umap'] = list(umap_embeddings_patentsberta)

/home/thiesen/Documents/Cleantech_Concepts/venv/lib64/python3.11/site-packages/umap/umap_.py:1943: UserWarning: n_jobs value -1 overridden to 1 by setting random_state. Use no seed for parallelism.
  warn(f"n_jobs value {self.n_jobs} overridden to 1 by setting random_state. Use no seed for parallelism.")


## t-SNE

In [29]:
import numpy as np
from openTSNE import TSNE
from sklearn.model_selection import train_test_split

In [30]:
# Generate train/test split
patentsberta_x_train, patentsberta_x_test = train_test_split(df_keywords_list_unique_embeddings['keyword_yake_patentsberta_embedding'].tolist(), test_size=0.2, random_state=42)
patentsberta_x_train_np = np.array(patentsberta_x_train)
patentsberta_x_test_np = np.array(patentsberta_x_test)

In [31]:
tsne = TSNE(
    perplexity=30,
    metric="euclidean",
    n_jobs=8,
    random_state=42,
    n_iter=1000,
    verbose=True,
)

In [32]:
# Perform t-SNE on training data
patentsberta_embedding_train = tsne.fit(patentsberta_x_train_np)

--------------------------------------------------------------------------------
TSNE(early_exaggeration=12, n_iter=1000, n_jobs=8, random_state=42,
     verbose=True)
--------------------------------------------------------------------------------
===> Finding 90 nearest neighbors using Annoy approximate search using euclidean distance...
   --> Time elapsed: 6.12 seconds
===> Calculating affinity matrix...
   --> Time elapsed: 0.09 seconds
===> Calculating PCA-based initialization...
   --> Time elapsed: 0.29 seconds
===> Running optimization with exaggeration=12.00, lr=1547.17 for 250 iterations...
Iteration   50, KL divergence 5.9806, 50 iterations in 0.5603 sec
Iteration  100, KL divergence 6.0037, 50 iterations in 0.5488 sec
Iteration  150, KL divergence 6.0041, 50 iterations in 0.5453 sec
Iteration  200, KL divergence 6.0041, 50 iterations in 0.5503 sec
Iteration  250, KL divergence 6.0041, 50 iterations in 0.5522 sec
   --> Time elapsed: 2.76 seconds
===> Running optimization w

In [33]:
patentsberta_embedding_test = patentsberta_embedding_train.transform(patentsberta_x_test_np)

===> Finding 15 nearest neighbors in existing embedding using Annoy approximate search...
   --> Time elapsed: 0.57 seconds
===> Calculating affinity matrix...
   --> Time elapsed: 0.00 seconds
===> Running optimization with exaggeration=4.00, lr=0.10 for 0 iterations...
   --> Time elapsed: 0.00 seconds
===> Running optimization with exaggeration=1.50, lr=0.10 for 250 iterations...
Iteration   50, KL divergence 57940.0190, 50 iterations in 0.8275 sec
Iteration  100, KL divergence 57395.6879, 50 iterations in 0.7959 sec
Iteration  150, KL divergence 57146.9347, 50 iterations in 0.7993 sec
Iteration  200, KL divergence 57010.4883, 50 iterations in 0.7888 sec
Iteration  250, KL divergence 56919.1995, 50 iterations in 0.7711 sec
   --> Time elapsed: 3.98 seconds


In [34]:
df_keywords_list_unique_embeddings_tsne = df_keywords_list_unique_embeddings.copy()

patentsberta_embedding = np.concatenate((patentsberta_embedding_train, patentsberta_embedding_test), axis=0)
df_keywords_list_unique_embeddings_tsne['keyword_yake_patentsberta_embedding_tsne'] = patentsberta_embedding.tolist()
df_keywords_list_unique_embeddings_tsne['keyword_yake_patentsberta_embedding_tsne_x'] = df_keywords_list_unique_embeddings_tsne['keyword_yake_patentsberta_embedding_tsne'].apply(lambda x: x[0])
df_keywords_list_unique_embeddings_tsne['keyword_yake_patentsberta_embedding_tsne_y'] = df_keywords_list_unique_embeddings_tsne['keyword_yake_patentsberta_embedding_tsne'].apply(lambda x: x[1])

# Clustering

In [35]:
# Import HDBSCAN
import hdbscan

In [40]:
# Ensure you're working on a new DataFrame, not a slice of an old one
df_keywords_list_unique_embeddings_hdbscan = df_keywords_list_unique_embeddings_tsne.copy()

# Perform HDBSCAN clustering on the UMAP coordinates
clusterer_patentsberta = hdbscan.HDBSCAN(min_cluster_size=100, min_samples=1).fit(df_keywords_list_unique_embeddings_hdbscan[['keyword_yake_patentsberta_embedding_tsne_x', 'keyword_yake_patentsberta_embedding_tsne_y']])

# Assign the cluster labels back to the DataFrame
df_keywords_list_unique_embeddings_hdbscan['patentsberta_cluster'] = clusterer_patentsberta.labels_

# Erase all rows with cluster -1
df_keywords_list_unique_embeddings_hdbscan = df_keywords_list_unique_embeddings_hdbscan[df_keywords_list_unique_embeddings_hdbscan['patentsberta_cluster'] != -1]

In [41]:
df_keywords_list_unique_embeddings_hdbscan.to_json('/mnt/hdd01/patentsview/Patentsview - Cleantech Patents/Cleantech Concepts/Yake/g_patent_claims_cleantech_yake_keywords_embeddings_tsne_hdbscan.json', orient='records')

# Plotting

In [38]:
import plotly.express as px

In [42]:
# Plot the UMAP embeddings in three figures, color coded by cluster
fig_patentsberta = px.scatter(
    df_keywords_list_unique_embeddings_hdbscan, 
    x='keyword_yake_patentsberta_embedding_tsne_x', 
    y='keyword_yake_patentsberta_embedding_tsne_y', 
    color='patentsberta_cluster', 
    hover_data=['patentsberta_cluster', 'keyword_yake'], 
    title='Cleantech Yake Keywords - HDBSCAN, TSNE, PatentSBERTa',
    height=800,  # Adjust as needed
    width=800    # Adjust as needed
)
# Display the figures
fig_patentsberta.show()

# fig_patentsberta.write_html('/mnt/hdd01/patentsview/Patentsview - Cleantech Patents/Cleantech Concepts/Yake/g_patent_claims_cleantech_yake_keywords_embeddings_tsne.html')

# Name Cluster

In [44]:
from transformers import pipeline, set_seed

In [45]:
# Build dataframe of keywords and their corresponding clusters, where each row is a cluster with list of keywords
df_keywords_clusters_patentsberta = df_keywords_list_unique_embeddings_hdbscan.groupby('patentsberta_cluster')['keyword_yake'].apply(list).reset_index(name='keywords')

In [46]:
# Initialize a text-generation pipeline with Flan-T5-large
import torch
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
generator = pipeline('text2text-generation', model='google/flan-t5-large', device=device)
set_seed(42)

In [62]:
def generate_cluster_name(keywords):
    # Ensure the keywords are in a list format
    keywords = keywords.split(', ') if isinstance(keywords, str) else keywords
    # Select only the first 1500 keywords from the list
    selected_keywords = keywords[:2000]
    # Join the selected keywords into a string format
    keywords_str = ', '.join(selected_keywords)
    # Create a prompt from the selected keywords
    # prompt = f"Based on the following keywords, come up with a specific, precise and short topic name: {keywords_str}"
    prompt = f"Generate a concise and descriptive common theme or category for a cluster containing the following keywords: {keywords_str}." # The name should be in title case and should not exceed three words."
    # Doesn't work at all -> only focuses on electric vehicle innovation# prompt = f"Given the keywords: {keywords_str}, provide a succinct cluster name similar to how 'Electric Vehicle Innovation' represents keywords like 'battery technology, electric motor, charging infrastructure'."
    # prompt = f"Identify a common theme or category for the following keywords: {keywords_str}. Provide a concise, descriptive name for this theme or category."
    # prompt = f"The keywords {keywords_str} all belong to the category: _____"
    # Generate a response using the GPT-3 model
    response = generator(prompt, max_length=10, do_sample=True, temperature=0.8)[0]['generated_text']
    # Extract the cluster name from the response
    cluster_name = response
    return cluster_name

# Apply the function to the 'keywords' column to generate cluster names
df_keywords_clusters_patentsberta['cluster_name'] = df_keywords_clusters_patentsberta['keywords'].progress_apply(generate_cluster_name)

  0%|          | 0/70 [00:00<?, ?it/s]/home/thiesen/Documents/Cleantech_Concepts/venv/lib64/python3.11/site-packages/transformers/pipelines/base.py:1101: UserWarning:

You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset

100%|██████████| 70/70 [00:15<00:00,  4.66it/s]


In [63]:
# Merge df_keywords_clusters_patentsberta with df_keywords_list_unique_pruned_embeddings_hdbscan on 'patentsberta_cluster'
df_keywords_list_unique_embeddings_cluster = pd.merge(df_keywords_list_unique_embeddings_hdbscan, df_keywords_clusters_patentsberta[['patentsberta_cluster', 'cluster_name']], on='patentsberta_cluster', how='left')

In [64]:
# Plotting
fig_patentsberta_cluster = px.scatter(
    df_keywords_list_unique_embeddings_cluster, 
    x='keyword_yake_patentsberta_embedding_tsne_x', 
    y='keyword_yake_patentsberta_embedding_tsne_y', 
    color='cluster_name', 
    hover_data=['patentsberta_cluster', 'keyword_yake'], 
    title='Cleantech Yake Keywords - HDBSCAN, TSNE, PatentSBERTa',
    height=800,  # Adjust as needed
    width=1200    # Adjust as needed
)

# Display the figures
fig_patentsberta_cluster.show()

In [70]:
# Arrange column order
df_keywords_clusters_patentsberta = df_keywords_clusters_patentsberta[['patentsberta_cluster', 'cluster_name', 'keywords']]

In [72]:
df_keywords_clusters_patentsberta.to_json('/mnt/hdd01/patentsview/Patentsview - Cleantech Patents/Cleantech Concepts/Yake/g_patent_claims_cleantech_yake_keywords_clusters_patentsberta.json', orient='records')

In [65]:
df_keywords_list_unique_embeddings_cluster.to_json('/mnt/hdd01/patentsview/Patentsview - Cleantech Patents/Cleantech Concepts/Yake/g_patent_claims_cleantech_yake_keywords_embeddings_tsne_hdbscan_cluster.json', orient='records')